# | default_exp Testing Polars for EDA, migrating cleaned data to Vespa

In [ ]:
# | hide
import adbc_driver_postgresql.dbapi
from datetime import datetime
from enum import Enum
import json
import polars as pl
import requests
from sqlalchemy import create_engine
from sqlalchemy.orm import sessionmaker
import vespa

1. Migrate data from postgres to vespa
   a. Need to do some data cleaning on the cuisines since there's typos
   Think postgres database can be a rawer form of the scrapes

In [ ]:
# make sure postgres is running!
# load postgres credentials
postgres_key_path = "../secrets/postgres_login.json"
with open(postgres_key_path, "r") as fo:
    postgres_key = json.loads(fo.read())
    user = postgres_key["user"]
    password = postgres_key["password"]
    host = postgres_key["host"]


In [ ]:
# try conncting to Postgresql with ADBC
uri = f"postgresql://{user}:{password}@{host}/mealeon"


In [ ]:
conn = adbc_driver_postgresql.dbapi.connect(uri)
with conn.cursor() as cur:
    cur.execute("SELECT * FROM recipe_scrapes LIMIT 2")
    print(cur.fetchone())

('AfricanBites-3f1a4fc7e099375adc6f06fbf4389396c3ad5bdfe4661a1980f0ee1143fe0317', 'English', '629883', 'Smoked Spatchcock Turkey', 'AfricanBites', 'https://www.africanbites.com/smoked-spatchcock-turkey/', ['salt and pepper for seasoning', '1 15-pound turkey', '4 tablespoons your choice of turkey rub (Creole, Italian, poultry, or your choice of seasoning)'], 'https://www.africanbites.com/wp-content/uploads/2021/08/IMG_9551-Copy-650x650.jpg', "Enjoy fall-off-the-bone goodness with flavorful juiciness in every bite. Simple smoking delivers flavor penetrating deep into your holiday bird without drying it out. This is your go-to guide for a deliciously tender and juicy turkey that's perfect any time of year!", ['Remove the giblet package.', 'Use your handy kitchen shears to cut the left side of the backbone from the tail to the neck. Do the same to the right side of the backbone. (A sharp knife will work as well.)', 'Flip the turkey over and press on it to break the breast bone and flatten 

In [ ]:
# first test, counting number of recipes from each site

query = """
    SELECT
        origin
        , COUNT(DISTINCT mealeon_id) AS num_recipes
    FROM recipe_scrapes
    GROUP BY origin
"""

df = pl.read_database_uri(query, uri, engine="adbc")

df.head()

shape: (4, 2)
┌─────────────────┬─────────────┐
│ origin          ┆ num_recipes │
│ ---             ┆ ---         │
│ str             ┆ i64         │
╞═════════════════╪═════════════╡
│ AfricanBites    ┆ 1491        │
│ AllRecipes      ┆ 4781        │
│ Epicurious      ┆ 4905        │
│ Panlasang_Pinoy ┆ 1938        │
└─────────────────┴─────────────┘

In [ ]:
# second test: unnesting the cuisine array and counting recipes per cuisine

query = """
    SELECT
        UNNEST(cuisines) AS cuisine
        , COUNT(DISTINCT mealeon_id) AS num_recipes
    FROM recipe_scrapes
    GROUP BY cuisine
"""

df = pl.read_database_uri(query, uri, engine="adbc")

df

shape: (885, 2)
┌────────────────────────┬─────────────┐
│ cuisine                ┆ num_recipes │
│ ---                    ┆ ---         │
│ str                    ┆ i64         │
╞════════════════════════╪═════════════╡
│ 30 Minutes or Less     ┆ 220         │
│ 5 Ingredients or Fewer ┆ 328         │
│ AFRICAN CARIBBEAN      ┆ 6           │
│ Absinthe               ┆ 6           │
│ Acorn Squash           ┆ 8           │
│ …                      ┆ …           │
│ Ziti                   ┆ 2           │
│ Zucchini               ┆ 36          │
│ dinner                 ┆ 1           │
│ soul                   ┆ 9           │
│ thanksgiving           ┆ 2           │
└────────────────────────┴─────────────┘

In [ ]:
with pl.Config(tbl_rows = -1):
    print(df)

shape: (885, 2)
┌─────────────────────────────────┬─────────────┐
│ cuisine                         ┆ num_recipes │
│ ---                             ┆ ---         │
│ str                             ┆ i64         │
╞═════════════════════════════════╪═════════════╡
│ 30 Minutes or Less              ┆ 220         │
│ 5 Ingredients or Fewer          ┆ 328         │
│ AFRICAN CARIBBEAN               ┆ 6           │
│ Absinthe                        ┆ 6           │
│ Acorn Squash                    ┆ 8           │
│ African                         ┆ 503         │
│ African-American                ┆ 1           │
│ African/Carribean               ┆ 3           │
│ Agua Fresca                     ┆ 6           │
│ Air Fryer                       ┆ 15          │
│ Alcohol                         ┆ 392         │
│ Aleppo-Style Pepper             ┆ 1           │
│ Almond                          ┆ 79          │
│ Almond Flour                    ┆ 6           │
│ Amaranth                        

In [ ]:
rename_cuisines = {
    "AFRICAN CARIBBEAN": "African-Caribbean",
    "African/Carribean": "African-Caribbean",
    "Carribean": "Caribbean",
    "Southern": "US Southern", 
    "soul": "Soul",
    "thanksgiving": "American",
    "dinner": "American",
    "New": "Fusion"
}

allowed_cuisines = {
    ""
}

# should World and International fall under Fusion?
# creation of super sets? ie: British has English, Irish, Scottish, Welsh. US Southern has Soul

In [ ]:
df.filter(pl.col('cuisine') == "dinner")

shape: (1, 2)
┌─────────┬─────────────┐
│ cuisine ┆ num_recipes │
│ ---     ┆ ---         │
│ str     ┆ i64         │
╞═════════╪═════════════╡
│ dinner  ┆ 1           │
└─────────┴─────────────┘

In [ ]:
df.filter(pl.col('cuisine') == "World")

shape: (1, 2)
┌─────────┬─────────────┐
│ cuisine ┆ num_recipes │
│ ---     ┆ ---         │
│ str     ┆ i64         │
╞═════════╪═════════════╡
│ World   ┆ 2           │
└─────────┴─────────────┘

In [ ]:
query = """
    SELECT
        mealeon_id
        , title
        , UNNEST(cuisines) AS cuisine
    FROM recipe_scrapes
"""

whole_df = pl.read_database_uri(query, uri, engine="adbc")

whole_df.filter(pl.col('cuisine') == 'dinner')

shape: (1, 3)
┌─────────────────────────────────┬─────────────────────────┬─────────┐
│ mealeon_id                      ┆ title                   ┆ cuisine │
│ ---                             ┆ ---                     ┆ ---     │
│ str                             ┆ str                     ┆ str     │
╞═════════════════════════════════╪═════════════════════════╪═════════╡
│ AfricanBites-d7711d944dfac2608… ┆ Smoked Beer Can Chicken ┆ dinner  │
└─────────────────────────────────┴─────────────────────────┴─────────┘

In [ ]:
# title "Smoked Beer Can Chicken" should become American

In [ ]:
whole_df.filter(pl.col('cuisine') == 'World')

shape: (2, 3)
┌─────────────────────────────────┬──────────────────────────────┬─────────┐
│ mealeon_id                      ┆ title                        ┆ cuisine │
│ ---                             ┆ ---                          ┆ ---     │
│ str                             ┆ str                          ┆ str     │
╞═════════════════════════════════╪══════════════════════════════╪═════════╡
│ AfricanBites-f6d10c8a7661af70d… ┆ How to Cook Jasmine Rice     ┆ World   │
│ AfricanBites-37edc9ea46a786a3b… ┆ How to Debone Chicken Thighs ┆ World   │
└─────────────────────────────────┴──────────────────────────────┴─────────┘

In [ ]:
whole_df.filter(pl.col('cuisine') == 'thanksgiving')

shape: (2, 3)
┌─────────────────────────────────┬──────────────────────┬──────────────┐
│ mealeon_id                      ┆ title                ┆ cuisine      │
│ ---                             ┆ ---                  ┆ ---          │
│ str                             ┆ str                  ┆ str          │
╞═════════════════════════════════╪══════════════════════╪══════════════╡
│ AfricanBites-95b6d113f5e590a53… ┆ Smoked Turkey Legs   ┆ thanksgiving │
│ AfricanBites-e94c35b5d5d62c1da… ┆ Smoked Turkey Breast ┆ thanksgiving │
└─────────────────────────────────┴──────────────────────┴──────────────┘

In [ ]:
whole_df.filter(pl.col('cuisine') == 'soul')

shape: (9, 3)
┌─────────────────────────────────┬─────────────────────────┬─────────┐
│ mealeon_id                      ┆ title                   ┆ cuisine │
│ ---                             ┆ ---                     ┆ ---     │
│ str                             ┆ str                     ┆ str     │
╞═════════════════════════════════╪═════════════════════════╪═════════╡
│ AfricanBites-f3e0779d8b9fa3c85… ┆ Chitterlings (Chitlins) ┆ soul    │
│ AfricanBites-00073465322187887… ┆ Hog Maw                 ┆ soul    │
│ AfricanBites-1bc8aa91a96c82547… ┆ Crispy Pork Jowl        ┆ soul    │
│ AfricanBites-c75aa5fb1e5a28aed… ┆ Ham Casserole           ┆ soul    │
│ AfricanBites-0076e7f4c79efd1e1… ┆ Pickled Pigs’ Feet      ┆ soul    │
│ AfricanBites-37a94e9f4db8d1dc3… ┆ Sweet Potato Biscuits   ┆ soul    │
│ AfricanBites-6f81180e7903637b2… ┆ Chicken Corn Chowder    ┆ soul    │
│ AfricanBites-4e1d69c66f031e599… ┆ Hoppin John             ┆ soul    │
│ AfricanBites-8761b8303d6685612… ┆ Air-Fryer Pork Chops    ┆ soul    │
└─────────────────────────────────┴─────────────────────────┴─────────┘

In [ ]:
whole_df.filter(pl.col('cuisine') == 'New')

shape: (89, 3)
┌─────────────────────────────────┬─────────────────────────────────┬─────────┐
│ mealeon_id                      ┆ title                           ┆ cuisine │
│ ---                             ┆ ---                             ┆ ---     │
│ str                             ┆ str                             ┆ str     │
╞═════════════════════════════════╪═════════════════════════════════╪═════════╡
│ AllRecipes-af169286bdd939a9e5e… ┆ Kiwi Fruit Salsa                ┆ New     │
│ AllRecipes-3440eb9d648fa5bea9a… ┆ Yummy Pikelets                  ┆ New     │
│ AllRecipes-11d30e76f14355834af… ┆ Shearers' Mince and Potato Hot… ┆ New     │
│ AllRecipes-e7642daa54b6e84c683… ┆ Dad's New Zealand Mince Stew    ┆ New     │
│ AllRecipes-7c91bff5430c2a2c412… ┆ Barbequed Thai Style Chicken    ┆ New     │
│ …                               ┆ …                               ┆ …       │
│ AllRecipes-1a4a1cafe5f2f5e9ee8… ┆ Keligun Chicken                 ┆ New     │
│ AllRecipes-9f5d8a8347394ba3782… ┆ Skite Cake                      ┆ New     │
│ AllRecipes-467c30863817f7dd199… ┆ Turkey Stir Fry with Lychees    ┆ New     │
│ AllRecipes-d72d9be6ebb2a8f01c3… ┆ Hamburger Sarah Style           ┆ New     │
│ AllRecipes-aa21ed15e2880755911… ┆ Dumplings and Cocky's Joy (Car… ┆ New     │
└─────────────────────────────────┴─────────────────────────────────┴─────────┘

In [ ]:
with pl.Config(tbl_rows = -1):
    print(whole_df.filter(pl.col('cuisine') == 'Missing Cuisine'))

shape: (2_060, 3)
┌─────────────────────────────────┬─────────────────────────────────┬─────────────────┐
│ mealeon_id                      ┆ title                           ┆ cuisine         │
│ ---                             ┆ ---                             ┆ ---             │
│ str                             ┆ str                             ┆ str             │
╞═════════════════════════════════╪═════════════════════════════════╪═════════════════╡
│ Epicurious-bafe135c3bb2cd9ea06… ┆ 43 Impressive Vegan Desserts f… ┆ Missing Cuisine │
│ Epicurious-1421c95a14fab4c1fcc… ┆ 83 Easy Summer Desserts         ┆ Missing Cuisine │
│ Epicurious-c29b348db0bde236ec7… ┆ 73 Finger Foods for Toddlers    ┆ Missing Cuisine │
│ Epicurious-382b5ae308c3559ce3f… ┆ The 8 Best Kitchen Tools For N… ┆ Missing Cuisine │
│ Epicurious-7b3c3b38d467e433b19… ┆ A Breastfeeding Parent's Snack… ┆ Missing Cuisine │
│ Epicurious-feafbd9ea5d23d83671… ┆ For Punchier Pantry Pasta, Add… ┆ Missing Cuisine │
│ Epicurious-1

In [ ]:
# leave Missing Cuisine as is, could be used as test data?

# now that we unpacked the cuisines, we actually want to fix some of these inconstencies

In [ ]:
rename_cuisines = {
    "AFRICAN CARIBBEAN": "African-Caribbean",
    "African/Carribean": "African-Caribbean",
    "Carribean": "Caribbean",
    "Southern": "US Southern", 
    "soul": "Soul",
    "thanksgiving": "American",
    "dinner": "American",
    "New": "Fusion"
}

whole_df = whole_df.with_columns(replaced=pl.col("cuisine").replace(rename_cuisines))

In [ ]:
whole_df

shape: (55_405, 4)
┌───────────────────────────────┬──────────────────────────────┬─────────────────┬─────────────────┐
│ mealeon_id                    ┆ title                        ┆ cuisine         ┆ replaced        │
│ ---                           ┆ ---                          ┆ ---             ┆ ---             │
│ str                           ┆ str                          ┆ str             ┆ str             │
╞═══════════════════════════════╪══════════════════════════════╪═════════════════╪═════════════════╡
│ AfricanBites-3f1a4fc7e099375a ┆ Smoked Spatchcock Turkey     ┆ Southern        ┆ US Southern     │
│ d…                            ┆                              ┆                 ┆                 │
│ AfricanBites-ad9870f668960462 ┆ How to Brine a Turkey        ┆ American        ┆ American        │
│ 4…                            ┆                              ┆                 ┆                 │
│ AfricanBites-9b119ba4403faa09 ┆ Refried Beans                ┆ Mexican         ┆ Mexican         │
│ 7…                            ┆                              ┆                 ┆                 │
│ AfricanBites-378e4cd9d9469919 ┆ Lemon Blueberry Scones       ┆ American        ┆ American        │
│ c…                            ┆                              ┆                 ┆                 │
│ AfricanBites-378e4cd9d9469919 ┆ Lemon Blueberry Scones       ┆ British         ┆ British         │
│ c…                            ┆                              ┆                 ┆                 │
│ …                             ┆ …                            ┆ …               ┆ …               │
│ Epicurious-c2d14b4a9c8ce565e0 ┆ Recipes From Bon Appétit’s   ┆ Missing Cuisine ┆ Missing Cuisine │
│ c…                            ┆ 202…                         ┆                 ┆                 │
│ Epicurious-6e1a2c4e1c055fdd6c ┆ Pesto Pasta with V8® Healthy ┆ Missing Cuisine ┆ Missing Cuisine │
│ 8…                            ┆ G…                           ┆                 ┆                 │
│ Epicurious-a3b0de4275f85201f5 ┆ Paprika Shrimp with Buttery  ┆ Missing Cuisine ┆ Missing Cuisine │
│ c…                            ┆ V8…                          ┆                 ┆                 │
│ Epicurious-02b70304b781f776b5 ┆ Sesame Oat Apple Crisp       ┆ Missing Cuisine ┆ Missing Cuisine │
│ 5…                            ┆                              ┆                 ┆                 │
│ Epicurious-01daa6bc5f9d7a741c ┆ Spiced Pear and Bourbon      ┆ Missing Cuisine ┆ Missing Cuisine │
│ 2…                            ┆ Sparkl…                      ┆                 ┆                 │
└───────────────────────────────┴──────────────────────────────┴─────────────────┴─────────────────┘

In [ ]:
with pl.Config(tbl_rows = -1):
    q = (
        whole_df.lazy()
        .group_by("replaced")
        .agg(
            pl.len().alias("recipe_count"),
            pl.col("cuisine", "title"),
        )
        .with_columns(pl.col("cuisine").list.unique().alias("unique_cuisines"), 
            )
        .sort("recipe_count", descending=True)
    )

    temp = q.collect()
    print(temp.select(pl.col('replaced', 'unique_cuisines')))

shape: (880, 2)
┌─────────────────────────────────┬─────────────────────────────────┐
│ replaced                        ┆ unique_cuisines                 │
│ ---                             ┆ ---                             │
│ str                             ┆ list[str]                       │
╞═════════════════════════════════╪═════════════════════════════════╡
│ Mexican                         ┆ ["Mexican"]                     │
│ Missing Cuisine                 ┆ ["Missing Cuisine"]             │
│ Filipino                        ┆ ["Filipino"]                    │
│ Cookbooks                       ┆ ["Cookbooks"]                   │
│ Nut Free                        ┆ ["Nut Free"]                    │
│ Vegetable                       ┆ ["Vegetable"]                   │
│ Dinner                          ┆ ["Dinner"]                      │
│ Easy                            ┆ ["Easy"]                        │
│ Vegetarian                      ┆ ["Vegetarian"]                  │
│ Gl

In [ ]:
# want to see how many recipes have more than one cuisine
# look in replaced, count the number in replaced, order by count descending

# with pl.Config(tbl_rows = -1):
#     q = (
#         whole_df.lazy()
#         # .group_by("replaced")
#         # .agg(
#         #     pl.len().alias("recipe_count"),
#         #     pl.col("cuisine", "title"),
#         # )
#         .with_columns(pl.col("replaced").list.len().alias("num_cuisines"), 
#             )
#         .sort("num_cuisines", descending=True)
#     )

#     temp = q.collect()
#     print(temp)

In [ ]:
# with pl.Config(tbl_rows = -1):
#     q = (
#         whole_df.lazy()
#         # .group_by("replaced")
#         # .agg(
#         #     pl.len().alias("recipe_count"),
#         #     pl.col("cuisine", "title"),
#         # )
#         .with_columns(pl.col("cuisine").list.len().alias("num_cuisines"), 
#             )
#         .sort("num_cuisines", descending=True)
#     )

#     temp = q.collect()
#     print(temp)

Unclear if there are actually multiple cuisines in some recipes or not. Scraper should've allowed that behavior since it's a list of strings, but let's look in postgres

In [ ]:
# unnesting the cuisine array and counting cuisines per recipe

query = """
    -- group recipe counts by cuisines counts
    SELECT
        num_cuisines
        , COUNT(DISTINCT mealeon_id) AS num_recipes
    FROM (
        -- unnest the cuisine array and count number of cuisines per recipe
        SELECT
            mealeon_id
            , CARDINALITY(cuisines) AS num_cuisines
        FROM recipe_scrapes
        GROUP BY mealeon_id
    ) cuisine_count
    GROUP BY num_cuisines
    ORDER BY num_cuisines DESC
"""

cuisine_counter_df = pl.read_database_uri(query, uri, engine="adbc")

cuisine_counter_df

shape: (35, 2)
┌──────────────┬─────────────┐
│ num_cuisines ┆ num_recipes │
│ ---          ┆ ---         │
│ i32          ┆ i64         │
╞══════════════╪═════════════╡
│ null         ┆ 1           │
│ 35           ┆ 2           │
│ 34           ┆ 2           │
│ 33           ┆ 3           │
│ 31           ┆ 3           │
│ …            ┆ …           │
│ 5            ┆ 18          │
│ 4            ┆ 11          │
│ 3            ┆ 110         │
│ 2            ┆ 206         │
│ 1            ┆ 9945        │
└──────────────┴─────────────┘

In [ ]:
# unnesting the cuisine array and counting cuisines per recipe

query = """
    -- group recipe counts by cuisines counts
    SELECT
        *
    FROM (
        -- unnest the cuisine array and count number of cuisines per recipe
        SELECT
            *
            , CARDINALITY(cuisines) AS num_cuisines
        FROM recipe_scrapes
        GROUP BY mealeon_id
    ) cuisine_count
    WHERE num_cuisines > 1 OR num_cuisines IS NULL
"""

cuisine_counter_df = pl.read_database_uri(query, uri, engine="adbc")

cuisine_counter_df

shape: (3_170, 12)
┌───────────┬──────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ mealeon_i ┆ language ┆ source_id ┆ title     ┆ … ┆ descripti ┆ steps     ┆ cuisines  ┆ num_cuisi │
│ d         ┆ ---      ┆ ---       ┆ ---       ┆   ┆ on        ┆ ---       ┆ ---       ┆ nes       │
│ ---       ┆ str      ┆ str       ┆ str       ┆   ┆ ---       ┆ list[str] ┆ list[str] ┆ ---       │
│ str       ┆          ┆           ┆           ┆   ┆ str       ┆           ┆           ┆ i32       │
╞═══════════╪══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ AfricanBi ┆ English  ┆ 662693    ┆ Hog Maw   ┆ … ┆ A robust, ┆ ["Thoroug ┆ ["soul",  ┆ 2         │
│ tes-00073 ┆          ┆           ┆           ┆   ┆ savory    ┆ hly wash  ┆ "Southern ┆           │
│ 465322187 ┆          ┆           ┆           ┆   ┆ dish      ┆ the hog   ┆ "]        ┆           │
│ 887…      ┆          ┆           ┆           ┆   ┆ bursting… ┆ maw …     ┆           ┆           │
│ AfricanBi ┆ English  ┆ 652850    ┆ Pickled   ┆ … ┆ Tender,   ┆ ["Wash    ┆ ["soul",  ┆ 2         │
│ tes-0076e ┆          ┆           ┆ Pigs’     ┆   ┆ tangy,    ┆ pigs'     ┆ "Southern ┆           │
│ 7f4c79efd ┆          ┆           ┆ Feet      ┆   ┆ and nutri ┆ feet thor ┆ "]        ┆           │
│ 1e1…      ┆          ┆           ┆           ┆   ┆ tious,…   ┆ oughly, … ┆           ┆           │
│ AfricanBi ┆ English  ┆ 624662    ┆ Summer    ┆ … ┆ Budget-fr ┆ []        ┆ ["America ┆ 3         │
│ tes-00c41 ┆          ┆           ┆ Pasta     ┆   ┆ iendly,   ┆           ┆ n", "Ital ┆           │
│ 128c7051c ┆          ┆           ┆ Recipes   ┆   ┆ kid-frien ┆           ┆ ian",     ┆           │
│ 143…      ┆          ┆           ┆           ┆   ┆ dly,…     ┆           ┆ "South…   ┆           │
│ AfricanBi ┆ English  ┆ 661486    ┆ Mississip ┆ … ┆ Rich,     ┆ ["Lightly ┆ ["America ┆ 2         │
│ tes-016c4 ┆          ┆           ┆ pi        ┆   ┆ zesty,    ┆ grease    ┆ n", "Sout ┆           │
│ 420eec473 ┆          ┆           ┆ Chicken   ┆   ┆ and       ┆ the       ┆ hern"]    ┆           │
│ b58…      ┆          ┆           ┆ Recipe    ┆   ┆ savory,   ┆ bottom    ┆           ┆           │
│           ┆          ┆           ┆           ┆   ┆ Missi…    ┆ of…       ┆           ┆           │
│ AfricanBi ┆ English  ┆ 680968    ┆ Cornbread ┆ … ┆ Crispy    ┆ ["Preheat ┆ ["America ┆ 2         │
│ tes-02990 ┆          ┆           ┆ With Corn ┆   ┆ edges, a  ┆ your oven ┆ n", "Sout ┆           │
│ 4f135e929 ┆          ┆           ┆           ┆   ┆ tender,   ┆ to 375°F  ┆ hern"]    ┆           │
│ 5b3…      ┆          ┆           ┆           ┆   ┆ moist …   ┆ (…        ┆           ┆           │
│ …         ┆ …        ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …         │
│ Epicuriou ┆ English  ┆ 626ec9849 ┆ Mutabbal  ┆ … ┆ The tahin ┆ ["Cook    ┆ ["Dip",   ┆ 16        │
│ s-ff6bfa7 ┆          ┆ ea8cd1feb ┆ (Eggplant ┆   ┆ i-laced   ┆ the       ┆ "Middle   ┆           │
│ dcd8ae90d ┆          ┆ 84929a    ┆ -Tahini   ┆   ┆ eggplant  ┆ eggplants ┆ Eastern", ┆           │
│ 5d3…      ┆          ┆           ┆ Dip)      ┆   ┆ vers…     ┆ directly  ┆ … "C…     ┆           │
│           ┆          ┆           ┆           ┆   ┆           ┆ …         ┆           ┆           │
│ Epicuriou ┆ English  ┆ 60464e751 ┆ Bamboo    ┆ … ┆ Mix up    ┆ ["For ind ┆ ["Cocktai ┆ 7         │
│ s-ff89f0e ┆          ┆ 5c0f4f277 ┆           ┆   ┆ this      ┆ ividual   ┆ l", "Alco ┆           │
│ deb5f6f5f ┆          ┆ 811f25    ┆           ┆   ┆ sherry    ┆ drinks,   ┆ hol", …   ┆           │
│ f15…      ┆          ┆           ┆           ┆   ┆ and       ┆ stir …    ┆ "Coo…     ┆           │
│           ┆          ┆           ┆           ┆   ┆ vermout…  ┆           ┆           ┆           │
│ Epicuriou ┆ English  ┆ 54a439436 ┆ Wassail   ┆ … ┆ Wassail   ┆ ["Combine ┆ ["Cocktai ┆ 24        │
│ s-ffa1023 ┆          ┆ 529d92b2c ┆      

So we know that there are recipes with more than 1 cuisines, `replace` text may be overriding? Need to make sure that replacement text goes back into an array of strings

In [ ]:
# rename_cuisines = {
#     "AFRICAN CARIBBEAN": "African-Caribbean",
#     "African/Carribean": "African-Caribbean",
#     "Carribean": "Caribbean",
#     "Southern": "US Southern", 
#     "soul": "Soul",
#     "thanksgiving": "American",
#     "dinner": "American",
#     "New": "Fusion"
# }

# whole_df = whole_df.with_columns(replaced_eval=pl.col("cuisine")
#                                  .list.eval(pl.element().replace(rename_cuisines))
#                                  )

In [ ]:
with pl.Config(tbl_rows = -1):
    q = (
        whole_df.lazy()
        .group_by("mealeon_id")
        .agg(
            pl.col("replaced")
            .alias("cleaned_cuisines"),
        )
    )

    temp = q.collect()
    print(temp)

shape: (13_114, 2)
┌─────────────────────────────────┬─────────────────────────────────┐
│ mealeon_id                      ┆ cleaned_cuisines                │
│ ---                             ┆ ---                             │
│ str                             ┆ list[str]                       │
╞═════════════════════════════════╪═════════════════════════════════╡
│ AfricanBites-1b0d897e3d2406616… ┆ ["Italian"]                     │
│ AfricanBites-d4d16f262aebd33e4… ┆ ["American"]                    │
│ Panlasang_Pinoy-2f1ec2d68ed912… ┆ ["Filipino"]                    │
│ Epicurious-1cf53dd9a830f97a0a3… ┆ ["Missing Cuisine"]             │
│ Epicurious-56cf16b0d2b2d344525… ┆ ["Missing Cuisine"]             │
│ AfricanBites-35286a9c17ee8d4b1… ┆ ["US Southern"]                 │
│ AllRecipes-144b0c7becf50285fb8… ┆ ["Indian"]                      │
│ AllRecipes-72fe01d92a72df786a4… ┆ ["African"]                     │
│ Epicurious-a4ae3d3d0ec5f662d9a… ┆ ["Missing Cuisine"]             │
│

Multiple approaches
1. I can join this dataframe with the original one (pulling from the server again) and joining the relabeled cuisine dataframe with the original one
2. Go back and do a list operation on the original data <-

In [ ]:
# pull all data

query = """
    SELECT
        *
    FROM recipe_scrapes
"""

all_data_df = pl.read_database_uri(query, uri, engine="adbc")

rename_cuisines = {
    "AFRICAN CARIBBEAN": "African-Caribbean",
    "African/Carribean": "African-Caribbean",
    "Carribean": "Caribbean",
    "Southern": "US Southern", 
    "soul": "Soul",
    "thanksgiving": "American",
    "dinner": "American",
    "New": "Fusion"
}

with pl.Config(tbl_rows = -1):
    q = (
        all_data_df.lazy()
        .with_columns(
            relabeled_cuisines = pl.col("cuisines").list.eval(pl.element().replace(rename_cuisines))
        )
    )


    temp = q.collect()
    print(temp)

shape: (13_115, 12)
┌───────────┬──────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ mealeon_i ┆ language ┆ source_id ┆ title     ┆ … ┆ descripti ┆ steps     ┆ cuisines  ┆ relabeled │
│ d         ┆ ---      ┆ ---       ┆ ---       ┆   ┆ on        ┆ ---       ┆ ---       ┆ _cuisines │
│ ---       ┆ str      ┆ str       ┆ str       ┆   ┆ ---       ┆ list[str] ┆ list[str] ┆ ---       │
│ str       ┆          ┆           ┆           ┆   ┆ str       ┆           ┆           ┆ list[str] │
╞═══════════╪══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ AfricanBi ┆ English  ┆ 629883    ┆ Smoked    ┆ … ┆ Enjoy fal ┆ ["Remove  ┆ ["Souther ┆ ["US Sout │
│ tes-3f1a4 ┆          ┆           ┆ Spatchcoc ┆   ┆ l-off-the ┆ the       ┆ n"]       ┆ hern"]    │
│ fc7e09937 ┆          ┆           ┆ k Turkey  ┆   ┆ -bone     ┆ giblet    ┆           ┆           │
│ 5ad…      ┆          ┆           ┆           ┆   ┆ goodne…   ┆ packag

In [ ]:
# temp.filter(
#     pl.col("relabeled_cuisines").list.len() > 1
# )


In [ ]:
# temp.filter(
#     pl.col("relabeled_cuisines").list.len() == 0
# )

In [ ]:
# temp.filter(
#     pl.col("cuisines").list.len() == 0
# )

In [ ]:
# temp.filter(
#     pl.col("relabeled_cuisines").is_null()
# )

We have successfully cleaned up the cuisine labels, should now migrate these futher cleaned recipes into Postgres and then Vespa to create embeddings

In [ ]:
# send dataframe back into Postgres
# cleaned_data_uri = f"postgresql://{user}:{password}@{host}/mealeon"

# temp.write_database(table_name="cleaned_recipes", connection=cleaned_data_uri, engine="adbc")

In [ ]:
# conn = adbc_driver_postgresql.dbapi.connect(cleaned_data_uri)
# with conn.cursor() as cur:
#     cur.execute("SELECT * FROM cleaned_recipes LIMIT 2")
#     print(cur.fetchone())

Whoops, didn't remove the original column

May need to check scraper: words with embedded links in the steps or ingredients may have been dropped 

In [ ]:
temp.drop_in_place("cuisines")


shape: (13_115,)
Series: 'cuisines' [list[str]]
[
	["Southern"]
	["American"]
	["Mexican"]
	["American", "British"]
	["Southern"]
	…
	["Missing Cuisine"]
	["Missing Cuisine"]
	["Missing Cuisine"]
	["Missing Cuisine"]
	["Missing Cuisine"]
]

In [ ]:
temp = temp.rename({"relabeled_cuisines": "cuisines"})

In [ ]:
print(temp)

shape: (13_115, 11)
┌───────────┬──────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ mealeon_i ┆ language ┆ source_id ┆ title     ┆ … ┆ photo_url ┆ descripti ┆ steps     ┆ cuisines  │
│ d         ┆ ---      ┆ ---       ┆ ---       ┆   ┆ ---       ┆ on        ┆ ---       ┆ ---       │
│ ---       ┆ str      ┆ str       ┆ str       ┆   ┆ str       ┆ ---       ┆ list[str] ┆ list[str] │
│ str       ┆          ┆           ┆           ┆   ┆           ┆ str       ┆           ┆           │
╞═══════════╪══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ AfricanBi ┆ English  ┆ 629883    ┆ Smoked    ┆ … ┆ https://w ┆ Enjoy fal ┆ ["Remove  ┆ ["US Sout │
│ tes-3f1a4 ┆          ┆           ┆ Spatchcoc ┆   ┆ ww.africa ┆ l-off-the ┆ the       ┆ hern"]    │
│ fc7e09937 ┆          ┆           ┆ k Turkey  ┆   ┆ nbites.co ┆ -bone     ┆ giblet    ┆           │
│ 5ad…      ┆          ┆           ┆           ┆   ┆ m/w…      ┆ goodne

In [ ]:
# send dataframe back into Postgres
cleaned_data_uri = f"postgresql://{user}:{password}@{host}/mealeon"

temp.write_database(table_name="cleaned_recipes", connection=cleaned_data_uri, engine="adbc", if_table_exists="replace")

13115

In [ ]:
print(temp)

shape: (13_115, 11)
┌───────────┬──────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ mealeon_i ┆ language ┆ source_id ┆ title     ┆ … ┆ photo_url ┆ descripti ┆ steps     ┆ cuisines  │
│ d         ┆ ---      ┆ ---       ┆ ---       ┆   ┆ ---       ┆ on        ┆ ---       ┆ ---       │
│ ---       ┆ str      ┆ str       ┆ str       ┆   ┆ str       ┆ ---       ┆ list[str] ┆ list[str] │
│ str       ┆          ┆           ┆           ┆   ┆           ┆ str       ┆           ┆           │
╞═══════════╪══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ AfricanBi ┆ English  ┆ 629883    ┆ Smoked    ┆ … ┆ https://w ┆ Enjoy fal ┆ ["Remove  ┆ ["US Sout │
│ tes-3f1a4 ┆          ┆           ┆ Spatchcoc ┆   ┆ ww.africa ┆ l-off-the ┆ the       ┆ hern"]    │
│ fc7e09937 ┆          ┆           ┆ k Turkey  ┆   ┆ nbites.co ┆ -bone     ┆ giblet    ┆           │
│ 5ad…      ┆          ┆           ┆           ┆   ┆ m/w…      ┆ goodne

Might have to dump to json, run conversion script, dump that to json

In [ ]:
# polars_export_path = "../data/raw/postgres_table_dump.json"
# temp.write_json(polars_export_path)

In [ ]:
temp.filter((pl.col("ingredients").len() < 1) | (pl.col("steps").len() < 1) | (pl.col("cuisines").len() < 1))

shape: (0, 11)
┌────────────┬──────────┬───────────┬───────┬───┬───────────┬─────────────┬───────────┬───────────┐
│ mealeon_id ┆ language ┆ source_id ┆ title ┆ … ┆ photo_url ┆ description ┆ steps     ┆ cuisines  │
│ ---        ┆ ---      ┆ ---       ┆ ---   ┆   ┆ ---       ┆ ---         ┆ ---       ┆ ---       │
│ str        ┆ str      ┆ str       ┆ str   ┆   ┆ str       ┆ str         ┆ list[str] ┆ list[str] │
╞════════════╪══════════╪═══════════╪═══════╪═══╪═══════════╪═════════════╪═══════════╪═══════════╡
└────────────┴──────────┴───────────┴───────┴───┴───────────┴─────────────┴───────────┴───────────┘

In [ ]:
temp.filter((pl.col("ingredients").is_null()) | (pl.col("steps").is_null()) | (pl.col("cuisines").is_null()))

shape: (1, 11)
┌───────────┬──────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ mealeon_i ┆ language ┆ source_id ┆ title     ┆ … ┆ photo_url ┆ descripti ┆ steps     ┆ cuisines  │
│ d         ┆ ---      ┆ ---       ┆ ---       ┆   ┆ ---       ┆ on        ┆ ---       ┆ ---       │
│ ---       ┆ str      ┆ str       ┆ str       ┆   ┆ str       ┆ ---       ┆ list[str] ┆ list[str] │
│ str       ┆          ┆           ┆           ┆   ┆           ┆ str       ┆           ┆           │
╞═══════════╪══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ AllRecipe ┆ English  ┆ 222014    ┆ "Pantry   ┆ … ┆ https://i ┆ I made    ┆ ["Preheat ┆ null      │
│ s-e556569 ┆          ┆           ┆ Raid"     ┆   ┆ magesvc.m ┆ this      ┆ the oven  ┆           │
│ d6282f106 ┆          ┆           ┆ Chicken   ┆   ┆ eredithco ┆ recipe up ┆ to 375    ┆           │
│ 23b…      ┆          ┆           ┆ Enchilad… ┆   ┆ rp.…      ┆ one nigh… ┆ degr…     ┆           │
└───────────┴──────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [ ]:
temp = temp.with_columns(pl.col("cuisines").fill_null(["Missing Cuisine"]))

In [ ]:
temp.filter((pl.col("ingredients").is_null()) | (pl.col("steps").is_null()) | (pl.col("cuisines").is_null()))

shape: (0, 11)
┌────────────┬──────────┬───────────┬───────┬───┬───────────┬─────────────┬───────────┬───────────┐
│ mealeon_id ┆ language ┆ source_id ┆ title ┆ … ┆ photo_url ┆ description ┆ steps     ┆ cuisines  │
│ ---        ┆ ---      ┆ ---       ┆ ---   ┆   ┆ ---       ┆ ---         ┆ ---       ┆ ---       │
│ str        ┆ str      ┆ str       ┆ str   ┆   ┆ str       ┆ str         ┆ list[str] ┆ list[str] │
╞════════════╪══════════╪═══════════╪═══════╪═══╪═══════════╪═════════════╪═══════════╪═══════════╡
└────────────┴──────────┴───────────┴───────┴───┴───────────┴─────────────┴───────────┴───────────┘

In [ ]:
# polars_export_path = "../data/raw/postgres_table_dump.json"
# temp.write_json(polars_export_path)

In [ ]:
# convert postgres records into Vespa format
# example structure of a record in vespa format
# vespa_record = {
#                 "put": f"id:{doc_type}:{doc_type}::{['recipe']['source']}-{record['id']}",
#                 "fields": {
#                     "origin": "epicurious", # replace with ['recipe']['source']
#                     "id": "",
#                     "title": "",
#                     "ingredients": "",
#                     "steps": "",
#                     "cuisine": "",
#                 },
#             }

# {"put": f"id:{doc_type}:{doc_type}::{record[mealeon_id]}",
#  "fields": {
#     "origin": record[origin], # not sure if needed, can just join with postgres
#     "id": record[source_id], # not sure if needed, can just join with postgres or use mealeon_id for join
#     "title": record[title], 
#     "ingredients": record[ingredients],
#     "steps": record[steps],
#     "description": record[description],
#     "cuisines": record[relabeled_cuisine]
#     }
# }

### Try mixing in PyVespa
Following documentation [here](https://pyvespa.readthedocs.io/en/latest/getting-started-pyvespa.html)

In [ ]:
from vespa.package import (
    ApplicationPackage,
    Field,
    Schema,
    Document,
    HNSW,
    RankProfile,
    Component,
    Parameter,
    FieldSet,
    GlobalPhaseRanking,
    Function,
    DocumentSummary,
    Summary
)

package = ApplicationPackage(
    name="mealeon2",
    schema=[
        Schema(
            name="mealeon2",
            document=Document(
                fields=[
                    Field(
                        name="language", 
                        type="string", 
                        indexing=["set_language"],
                        # match=["word"]
                    ),
                    Field(
                        name="id",
                        type="string",
                        indexing=["attribute", "summary"],
                        match=["word"],
                        bolding=True,
                    ),
                    Field(
                        name="title",
                        type="string",
                        indexing=["index", "summary"],
                        index="enable-bm25",
                        match=["word"]
                    ), 
                    Field(
                        name="description",
                        type="string",
                        indexing=["index"],
                        index="enable-bm25",
                        match=["word"],
                    ),                 
                    Field(
                        name="ingredients",
                        type="array<string>",
                        indexing=["index", "attribute"],
                        # attribute="fast-search",
                        index="enable-bm25",
                        # match=["word"],
                    ),
                    Field(
                        name="steps",
                        type="array<string>",
                        indexing=["index", "attribute"],
                        index="enable-bm25"
                    ),
                    Field(
                        name="cuisines",
                        type="array<string>",
                        indexing=["index", "attribute", "summary"],
                        index="enable-bm25",
                        match=["text"],
                    ),
                    # Field(
                    #     name="embedding",
                    #     type="tensor<float>(x[384])",
                    #     indexing=[
                    #         'input title . " " . input body',
                    #         "embed",
                    #         "index",
                    #         "attribute",
                    #     ],
                    #     ann=HNSW(distance_metric="angular"),
                    #     is_document_field=False,
                    # ),
                ]
            ),
            fieldsets=[
                FieldSet(
                    name="default", 
                    fields=["title", "ingredients"]
                )
            ],
            document_summaries=[
                    DocumentSummary(
                    name="document-summary",
                    summary_fields=[
                        Summary("id")
                    ]
                ),
            ],
            rank_profiles=[
                RankProfile(
                    name="default",
                    first_phase="nativeRank(title, ingredients)"
                ),
                RankProfile(
                    name="bm25",
                    inherits="default",
                    first_phase="bm25(title) + bm25(ingredients)",
                    # inputs=[("query(q)", "tensor<float>(x[384])")],
                    functions=[
                        Function(name="bm25sum", expression="bm25(title) + bm25(ingredients)")
                    ],
                ),
                RankProfile(
                    name="combined", 
                    inherits="default",
                    first_phase="bm25(title) + bm25(ingredients) + nativeRank(title) + nativeRank(ingredients)",
                    functions=[
                        Function(name="bm25nativeRank",
                                 expression="bm25(title) + bm25(ingredients) + nativeRank(title) + nativeRank(ingredients)")
                    ]
                )
                # RankProfile(
                #     name="semantic",
                #     inputs=[("query(q)", "tensor<float>(x[384])")],
                #     first_phase="closeness(field, embedding)",
                # ),
                # RankProfile(
                #     name="fusion",
                #     inherits="bm25",
                #     inputs=[("query(q)", "tensor<float>(x[384])")],
                #     first_phase="closeness(field, embedding)",
                #     global_phase=GlobalPhaseRanking(
                #         expression="reciprocal_rank_fusion(bm25sum, closeness(field, embedding))",
                #         rerank_count=1000,
                #     ),
                # ),
            ],
        )
    ],
    # components=[
    #     Component(
    #         id="e5",
    #         type="hugging-face-embedder",
    #         parameters=[
    #             Parameter(
    #                 "transformer-model",
    #                 {
    #                     "url": "https://github.com/vespa-engine/sample-apps/raw/master/simple-semantic-search/model/e5-small-v2-int8.onnx"
    #                 },
    #             ),
    #             Parameter(
    #                 "tokenizer-model",
    #                 {
    #                     "url": "https://raw.githubusercontent.com/vespa-engine/sample-apps/master/simple-semantic-search/model/tokenizer.json"
    #                 },
    #             ),
    #         ],
    #     )
    # ],
)

In [ ]:
# try mixing in PyVespa

from vespa.deployment import VespaDocker

vespa_docker = VespaDocker(port=8182,
                           cfgsrv_port=19091)
app = vespa_docker.deploy(application_package=package)


Waiting for configuration server, 0/300 seconds...
Waiting for configuration server, 5/300 seconds...
Using plain http against endpoint http://localhost:8182/ApplicationStatus
Waiting for application status, 0/300 seconds...
Using plain http against endpoint http://localhost:8182/ApplicationStatus
Waiting for application status, 5/300 seconds...
Using plain http against endpoint http://localhost:8182/ApplicationStatus
Waiting for application status, 10/300 seconds...
Using plain http against endpoint http://localhost:8182/ApplicationStatus
Waiting for application status, 15/300 seconds...
Using plain http against endpoint http://localhost:8182/ApplicationStatus
Waiting for application status, 20/300 seconds...
Using plain http against endpoint http://localhost:8182/ApplicationStatus
Waiting for application status, 25/300 seconds...
Using plain http against endpoint http://localhost:8182/ApplicationStatus
Application is up!
Finished deployment.


In [ ]:
!vespa feed ../data/raw/postgres_mealeon_vespa.json --target http://localhost:8182

{
  "feeder.operation.count": 13115,
  "feeder.seconds": 15.250,
  "feeder.ok.count": 13115,
  "feeder.ok.rate": 859.992,
  "feeder.error.count": 0,
  "feeder.inflight.count": 0,
  "http.request.count": 13115,
  "http.request.bytes": 11253214,
  "http.request.MBps": 0.738,
  "http.exception.count": 0,
  "http.response.count": 13115,
  "http.response.bytes": 3041794,
  "http.response.MBps": 0.199,
  "http.response.error.count": 0,
  "http.response.latency.millis.min": 10,
  "http.response.latency.millis.avg": 48,
  "http.response.latency.millis.max": 446,
  "http.response.code.counts": {
    "200": 13115
  }
}


In [ ]:
from vespa.io import VespaResponse, VespaQueryResponse

# query should be recipe name?
    # WHERE title !contains {query}
# cuisine name should be in the WHERE filter clause of YQL
    # AND WHERE cuisine NOT IN {cuisines}
# how to penalize similar title?

# start with plain keyword search

with app.syncio(connections=1) as session:
    query = "Buffalo Wings"
    response: VespaQueryResponse = session.query(
        yql=f"select * from sources mealeon2 where (title contains '{query}') limit 10",
        query=query,
        ranking="bm25"
        # body={"input.query(q)": f"embed({query})"},
    )
    assert response.is_successful()

In [ ]:
print(response.hits)

[{'id': 'id:mealeon2:mealeon2::Epicurious-1c0fe6496b26a8b7bdf549e9ed70bc9802d7df404b89f1d3de6d01a1a44d31f8', 'relevance': 9.076123029856374, 'source': 'mealeon2_content', 'fields': {'sddocname': 'mealeon2', 'id': 'Epicurious-1c0fe6496b26a8b7bdf549e9ed70bc9802d7df404b89f1d3de6d01a1a44d31f8', 'documentid': 'id:mealeon2:mealeon2::Epicurious-1c0fe6496b26a8b7bdf549e9ed70bc9802d7df404b89f1d3de6d01a1a44d31f8', 'title': 'Buffalo Wings', 'cuisines': ['Gourmet', 'Super Bowl', 'Hot Sauce', 'Condiment', 'American', 'Chicken Wing', 'Chicken', 'Poultry', 'Yogurt', 'Dairy', 'Main', 'Starter', 'Dinner', 'Lunch', 'Gluten Free', 'Nut Free', 'Keto', 'Deep Fry']}}]


In [ ]:
next_resp_json = next_resp.json()
next_resp_json

NameError: name 'next_resp' is not defined

In [ ]:
# actual results
results = resp_json['hits']
results

In [ ]:
# | hide
nbdev.nbdev_export()